# Level 2 Script

Combine Level 1 output with level 2 features and create final ranking

In [11]:
# import section
import pickle

import pandas as pd

from pandas.testing import assert_frame_equal
from sklearn.cluster import KMeans
from sklearn import preprocessing
from skimage.color import rgb2lab, deltaE_cie76

import matplotlib.pyplot as plt
import numpy as np
import cv2
from collections import Counter

import os
import requests
import urllib.request
%matplotlib inline
import socket
import imutils 
from skimage.measure import compare_ssim as ssim
from colorthief import ColorThief
from sklearn import preprocessing
from skimage.transform import resize
from skimage.metrics import structural_similarity
from skimage.measure import compare_ssim

import nltk
import difflib
import datetime

### Functions

In [12]:
# create list of paths to book covers
def create_trains_paths(folder_path):
    train_paths = []
    train_path = folder_path
    for root, dirs, files in os.walk(train_path):
         for file in files:
            train_paths.append((os.path.join(root, file)))
    return train_paths        

In [13]:
# create histograms for all covers
def create_histograms(train_paths):
    hist_train = []
    for path in train_paths:
        image = cv2.imread(path)

        if image is None:
            continue
        image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        # extract a RGB color histogram from the image,
        # using 8 bins per channel, normalize, and update
        # the index
        hist = cv2.calcHist([image], [0, 1, 2], None, [8, 8, 8],[0, 256, 0, 256, 0, 256])
        hist = cv2.normalize(hist, None)
        hist_train.append((path,hist))
    return hist_train    

In [14]:
# code to compute mean structural similarity index between two images with compare_ssim()
def create_structural_similarity(df):
    structural_similarity = []
    recommendations = df
    for i in range(0, len(recommendations)):
        print(i)

        itemID_path = recommendations.iloc[i]['itemId_path']
        recID_path = recommendations.iloc[i]['rec_id_path']


        img00 = cv2.imread(itemID_path, 0)
        img01 = cv2.imread(recID_path, 0)

        if (img00 is None) or (img01 is None):
            print("at least one pic is None")
            structural_similarity.append(np.NaN)

        else:
            # compute structural similarity        
            #resize rec picture so both have same dimension
            img011 = resize(img01, (img00.shape[0], img00.shape[1]), anti_aliasing=True, preserve_range=True)
            ssim = compare_ssim(img00, img011) #1.0 means identical. Lower = not similar

            print("Similarity using SSIM is: ", ssim)
            structural_similarity.append(ssim)
    return structural_similarity            

In [15]:
# compute histogram correlation
def create_hist_correlation(df, hist_train):
    
    recommendations = df
    hist_correlation = []
    #orb_similarity = []
    #structural_similarity = []

    for i in range(0, len(recommendations)):
        print(i)

        itemID_path = recommendations.iloc[i]['itemId_path']
        recID_path = recommendations.iloc[i]['rec_id_path']

        #itemID_hist_path = np.NaN
        #recID_hist_path = np.NaN
        for j in range(len(hist_train)):
            if itemID_path == hist_train[j][0]:
                itemID_hist_path = hist_train[j][0]
                index_itemID_hist_path = j
            if recID_path == hist_train[j][0]:
                recID_hist_path = hist_train[j][0] 
                index_recID_hist_path = j

        # we have found ID matches for item and rec
        # now we compare histograms:

        try:
            # histogram match could be found! -> calculate correlation
            cmp = cv2.compareHist(hist_train[index_itemID_hist_path][1], hist_train[index_recID_hist_path][1], cv2.HISTCMP_CORREL)
            hist_correlation.append(cmp)
            print('match was found: \n' + 
                   itemID_path + ', ' + itemID_hist_path + '\n' + 
                   recID_path  + ', ' + recID_hist_path)

        except:
            # histogram match could not be found -> 
            print('no match found / covers do not exist in folder')
            hist_correlation.append(np.NaN)
    return hist_correlation

In [16]:
# get main color for ITEM
def create_main_color_item(df):
    recommendations = df
    colorlist = []
    count = 0
    for path in recommendations['itemId_path']:
        print(count)
        count += 1
        #image = cv2.imread(path)

        #if image is None:
        #    continue
        try:
            #image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
            color_thief = ColorThief(path)
            dominant_color = color_thief.get_color(quality=1)
            #palette = color_thief.get_palette(color_count=6)
            colorlist.append(dominant_color)
        except:
            print('error occured with ' + str(path))
            colorlist.append(np.NaN)
    return colorlist            

In [17]:
# get main color for RECOMMENDATION
def create_main_color_rec(df):
    recommendations = df
    colorlist_rec = []
    count = 0
    for path in recommendations['rec_id_path']:
        print(count)
        count += 1
        #image = cv2.imread(path)

        #if image is None:
        #    continue
        try:
            #image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
            color_thief = ColorThief(path)
            dominant_color = color_thief.get_color(quality=1)
            #palette = color_thief.get_palette(color_count=6)
            colorlist_rec.append(dominant_color)
        except:
            print('error occured with ' + str(path))
            colorlist_rec.append(np.NaN)
    return colorlist_rec                   

In [18]:
# calculate Euclidean Distance between main colors of item and recommendation
def create_main_color_euc_dist(df):
    recommendations = df
    color_euc_dist = []
    for i in range(0, len(recommendations)):
        tuple1 = recommendations.iloc[i]['itemID_color']
        tuple2 = recommendations.iloc[i]['recID_color']
        print(i)
        try:
            euc_dist = np.sqrt((tuple1[0] - tuple2[0])**2 + (tuple1[1] - tuple2[1])**2 + (tuple1[2] - tuple2[2])**2)
            color_euc_dist.append(euc_dist)
        except:
            print('at least one time NAN')
            color_euc_dist.append(np.NaN)
    return color_euc_dist        

In [19]:
# find categories matches
# insert 1 if match 
# insert 0 if no match
def create_categories_match(df):
    categories_match = df
    categories_match['category_match'] = np.NaN
    for i in range(0, len(categories_match)):
        if categories_match.iloc[i]['g_categories_item'] == categories_match.iloc[i]['g_categories_rec']:
            check = 1
        else:
            check = 0
        categories_match.at[i, 'category_match'] = check
    return categories_match['category_match']    

In [20]:
# create main topic match
def create_main_topic_match(df):
    rec_categories_maintopic_subtopic = df
    rec_categories_maintopic_subtopic['main_topic_match'] = np.NaN
    for i in range(0, len(rec_categories_maintopic_subtopic)):
        if rec_categories_maintopic_subtopic.iloc[i]['main_topic_item'] == rec_categories_maintopic_subtopic.iloc[i]['main_topic_rec']:
            check = 1
        else:
            check = 0
        rec_categories_maintopic_subtopic.at[i, 'main_topic_match'] = check
    return rec_categories_maintopic_subtopic['main_topic_match']

In [21]:
def create_main_topic_levenshtein(df):
    rec_categories_maintopic_subtopic = df
    # alternative: create score by how simiilar letters of a string are 
    #rec_categories_maintopic_subtopic['main_topic_levenstein'] = np.NaN
    rec_categories_maintopic_subtopic['main_topic_seqmatch'] = np.NaN
    for i in range(0, len(rec_categories_maintopic_subtopic)):
        main_item = rec_categories_maintopic_subtopic.iloc[i]['main_topic_item']
        main_rec = rec_categories_maintopic_subtopic.iloc[i]['main_topic_rec']
        #dist = nltk.edit_distance("main_item", "main_rec")
        seq = difflib.SequenceMatcher(None,main_item,main_rec)
        d = seq.ratio()
        #rec_categories_maintopic_subtopic.at[i, 'main_topic_levenstein'] = dist
        rec_categories_maintopic_subtopic.at[i, 'main_topic_seqmatch'] = d
    return rec_categories_maintopic_subtopic['main_topic_seqmatch']

In [22]:
# find categories matches
# insert 1 if match 
# insert 0 if no match
def create_main_topic_cluster_match(df):
    categories_match = df
    categories_match['main_topic_cluster_match'] = np.NaN
    for i in range(0, len(categories_match)):
        if categories_match.iloc[i]['main_topic_cluster_item'] == categories_match.iloc[i]['main_topic_cluster_rec']:
            check = 1
        else:
            check = 0
        categories_match.at[i, 'main_topic_cluster_match'] = check
    return categories_match['main_topic_cluster_match']    

In [23]:
def count_subtopic_matches(df):
    rec_categories_maintopic_subtopic = df

    # count matches in suptopics
    #rec_categories_maintopic_subtopic['']
    rec_categories_maintopic_subtopic['suptopics_matches_count'] = np.NaN
    rec_categories_maintopic_subtopic['suptopics_matches_weight'] = np.NaN
    
    #rec_categories_maintopic_subtopic.loc[rec_categories_maintopic_subtopic.isnull()] = rec_categories_maintopic_subtopic.loc[rec_categories_maintopic_subtopic.isnull()].apply(lambda subtopics_item: [])
    #rec_categories_maintopic_subtopic.loc[rec_categories_maintopic_subtopic.isnull()] = rec_categories_maintopic_subtopic.loc[rec_categories_maintopic_subtopic.isnull()].apply(lambda subtopics_rec: [])    
    
    for i in range(0, len(rec_categories_maintopic_subtopic)):
        list_item = rec_categories_maintopic_subtopic.iloc[i]['subtopics_item']
        list_rec = rec_categories_maintopic_subtopic.iloc[i]['subtopics_rec']
        print(list_item)       
        print(list_rec)       
        
        #if (pd.isnull(list_item) == True) or (pd.isnull(list_rec) == True):
         #   rec_categories_maintopic_subtopic.at[i, 'suptopics_matches_count'] = np.NaN
          #  rec_categories_maintopic_subtopic.at[i, 'suptopics_matches_weight'] = np.NaN   
        
        if (len(list_item)>2) and (len(list_rec)>2):
            list_item = list_item.strip('][').split(',')#[1:-1].split(',')
            list_rec = list_rec.strip('][').split(',')#[1:-1].split(',')
            print(str(list_item) + ', ' + str(list_rec))
            try:
                # count how many elements are in both lists
                count = len([key for key, val in enumerate(list_item) if val in set(list_rec)])
                print(count)
                # create a relative score by dividing by the average length of the lists
                length = (len(list_item) + len(list_rec)) / 2
                weight = count / length
                rec_categories_maintopic_subtopic.at[i, 'suptopics_matches_count'] = count
                rec_categories_maintopic_subtopic.at[i, 'suptopics_matches_weight'] = weight
            except:
                rec_categories_maintopic_subtopic.at[i, 'suptopics_matches_count'] = 0
                rec_categories_maintopic_subtopic.at[i, 'suptopics_matches_weight'] = 0            
                print('counter does not run' + str(list_item) + ', ' + str(list_rec))
        else:
            print('one is too short' + str(list_item) + ', ' + str(list_rec))
            rec_categories_maintopic_subtopic.at[i, 'suptopics_matches_count'] = 0
            rec_categories_maintopic_subtopic.at[i, 'suptopics_matches_weight'] = 0        
    return rec_categories_maintopic_subtopic[['suptopics_matches_count', 'suptopics_matches_weight']]

In [24]:
# get publish year of book
def get_publish_year(df):
    items_ex = df
    items_ex['year'] = np.NaN
    for i in range(0, len(items_ex)):
        try:
            date = items_ex.iloc[i]['dates']
            if len(date) == 1:
                date = date[0]
                year = date.year
                items_ex.at[i,'year'] = year
            elif len(date) == 2:
                date1 = date[0]
                date2 = date[1]
                year1 = date1.year
                year2 = date2.year
                if year1 <= year2:
                    items_ex.at[i,'year'] = year1
                else:
                    items_ex.at[i,'year'] = year2
        except:
            items_ex.at[i,'year'] = np.NaN
    return items_ex['year']      

### Step 0: define all relevant parameters

In [184]:
# insert the path where the book covers are saved
train_path = "/Users/MaxLangeMac/Desktop/Semester 3/Data Mining/DMC-2021-Task/Cover_Pics_Ext_Final"

# folder where book covers are saved
folder = '/Users/MaxLangeMac/Desktop/Semester 3/Data Mining/DMC-2021-Task/Cover_Pics_Ext_Final/'


### Step 1: Get necessary data

In [25]:
# load recommendations from level 1 - pickle
#with open('finalresults_example_20210616.pkl', 'rb') as f:
#    rec = pickle.load(f)

In [26]:
# load recommendation from level 1 - csv

rec = pd.read_csv('cleanedRecommendations_20210628.csv')

In [27]:
# sort recommendations by itemID, then by weight so best recommendation comes first
rec = rec.sort_values(by=['itemId', 'weight'], ascending = (True, False))

In [28]:
# read in external data
items_ex = pd.read_pickle('External_Data_incl_Features.pkl')
items_ex = items_ex.reset_index()

In [29]:
# load topic clusters from pickle file
with open('main_topic_clusters.pkl', 'rb') as f:
    clusters = pickle.load(f)

### Step 2: Create Level 2 Features

#### Cover Analysis

In [196]:
# save paths to book covers in list
train_paths = create_trains_paths(train_path)

In [197]:
hist_train = create_histograms(train_paths)

KeyboardInterrupt: 

In [ ]:
# add paths to rec dataframe
rec['itemId'] = rec['itemId'].astype('int')
rec['rec_id'] = rec['rec_id'].astype('int')
rec['itemId_path'] = folder + rec['itemId'].astype(str) + '.jpg'
rec['rec_id_path'] = folder + rec['rec_id'].astype(str) + '.jpg'

In [ ]:
# add structural similarity between item and rec as feature to dataframe
rec['structural_similarity'] = create_structural_similarity(rec)

In [ ]:
# add histogram correlation feature to recommendations dataframe
rec['hist_correlation'] = create_hist_correlation(rec, hist_train)

In [28]:
# add main color of item as feature to recommendations dataframe
#rec['itemID_color'] = create_main_color_item(rec)

In [29]:
# add rec main colour as column to recommendations dataframe
#rec['recID_color'] = create_main_color_rec(rec)

In [30]:
# create feature out of main colors
"""
rec['main_color_euc_distance'] = create_main_color_euc_dist(rec)

# normalization of Euclidean distance 
values = rec['main_color_euc_distance'].values
min_max_scaler = preprocessing.MinMaxScaler()
null_index = rec['main_color_euc_distance'].isnull()
rec.loc[~null_index, ['main_color_euc_distance_norm']] = min_max_scaler.fit_transform(rec.loc[~null_index, ['main_color_euc_distance']])
rec['main_color_euc_distance_norm'] = (rec['main_color_euc_distance_norm']-1)*(-1)
"""

"\nrec['main_color_euc_distance'] = create_main_color_euc_dist(rec)\n\n# normalization of Euclidean distance \nvalues = rec['main_color_euc_distance'].values\nmin_max_scaler = preprocessing.MinMaxScaler()\nnull_index = rec['main_color_euc_distance'].isnull()\nrec.loc[~null_index, ['main_color_euc_distance_norm']] = min_max_scaler.fit_transform(rec.loc[~null_index, ['main_color_euc_distance']])\nrec['main_color_euc_distance_norm'] = (rec['main_color_euc_distance_norm']-1)*(-1)\n"

#### external data analysis

In [198]:
#### checkpoint:
# save rec in other df to secure it if sth goes wrong
rec2 = rec

In [199]:
# set back:
rec = rec2

In [200]:
### save the so far recommendations 
with open('recommendations_cover_level2_script.pkl', 'wb') as f:
    pickle.dump(rec2, f)

In [201]:
# load recommendations from level 1
with open('recommendations_cover_level2_script.pkl', 'rb') as f:
    rec = pickle.load(f)

###### page count feature

In [203]:
# two sources of pages
# first preprocess pages data
items_ex[['pages1','pages2']] = pd.DataFrame(items_ex.pages.tolist(), index= items_ex.index)

# pre-process for calculation
items_ex['pages1'] = pd.to_numeric(items_ex["pages1"], downcast="float")
items_ex['pages2'] = pd.to_numeric(items_ex["pages2"], downcast="float")

# get mean of pages
items_ex['pages_mean'] = items_ex.loc[:,'pages1':'pages2'].mean(axis=1)

In [204]:
### now create a level 2 feature out of pages in recommendation dataframe

# insert pages of itemID
rec = rec.merge(items_ex[['itemID', 'pages_mean']], left_on = 'itemId', right_on = 'itemID', how = 'left')

# insert pages of rec
rec = rec.merge(items_ex[['itemID', 'pages_mean']], left_on = 'rec_id', right_on = 'itemID', how = 'left')

# rename columns
rec = rec.rename(columns= {'pages_mean_x': 'pages_mean_item',
                            #'pageCount_scaled_x': 'pageCount_scaled_item',
                            'pages_mean_y': 'pages_mean_rec'
                            #'pageCount_scaled_y': 'pageCount_scaled_rec'
                                                              })

# drop unnecessary columns
rec = rec.drop(['itemID_x', 'itemID_y'], axis = 1)

### finally, create feature
# get 1 of the 2 books that has higher pages count
rec['max_pageCount'] = rec[["pages_mean_item", "pages_mean_rec"]].max(axis=1)
# calculate euclidean distance between the 2 books' pages
rec['Euc_distance'] = np.sqrt((rec['pages_mean_item'] - rec['pages_mean_rec'])**2)
# create relative distance between 2 books' pages
rec['rel_distance'] = rec['Euc_distance']/rec['max_pageCount']
# create final score by inverting (the higher the score the smaller the relative distance between the 2 books' pages)
rec['score'] = (rec['rel_distance']-1)*(-1)

##### categories feature

In [32]:
### get g_categories

# merge items with feature
rec = rec.merge(items_ex[['itemID', 'g_categories']], left_on = 'itemId', right_on = 'itemID', how = 'left')

# merge recs with feature
rec = rec.merge(items_ex[['itemID', 'g_categories']], left_on = 'rec_id', right_on = 'itemID', how = 'left')

# rename columns 
rec = rec.rename(columns= {'g_categories_x': 'g_categories_item',
                            #'pageCount_scaled_x': 'pageCount_scaled_item',
                           'g_categories_y': 'g_categories_rec'
                            #'pageCount_scaled_y': 'pageCount_scaled_rec'
                                                              })
# drop unnecessary columns
rec = rec.drop(['itemID_x', 'itemID_y'], axis = 1)

In [33]:
### get main topic

# merge items with feature
rec = rec.merge(items_ex[['itemID', 'main topic']], left_on = 'itemId', right_on = 'itemID', how = 'left')

# merge recs with feature
rec = rec.merge(items_ex[['itemID', 'main topic']], left_on = 'rec_id', right_on = 'itemID', how = 'left')

# rename columns 
rec = rec.rename(columns= {'main topic_x': 'main_topic_item',
                            #'pageCount_scaled_x': 'pageCount_scaled_item',
                            'main topic_y': 'main_topic_rec'
                            #'pageCount_scaled_y': 'pageCount_scaled_rec'
                                                              })
# drop unnecessary columns
rec = rec.drop(['itemID_x', 'itemID_y'], axis = 1)


In [34]:
### get sub topics

# merge items with feature
rec = rec.merge(items_ex[['itemID', 'subtopics']], left_on = 'itemId', right_on = 'itemID', how = 'left')

# merge recs with feature
rec = rec.merge(items_ex[['itemID', 'subtopics']], left_on = 'rec_id', right_on = 'itemID', how = 'left')

# rename columns 
rec = rec.rename(columns= {'subtopics_x': 'subtopics_item',
                             #'pageCount_scaled_x': 'pageCount_scaled_item',
                            'subtopics_y': 'subtopics_rec'
                            #'pageCount_scaled_y': 'pageCount_scaled_rec'
                                                              })
# drop unnecessary columns
rec = rec.drop(['itemID_x', 'itemID_y'], axis = 1)


In [35]:
### prepare description clusters

# merge items with feature
rec = rec.merge(clusters[['itemID', 'main_topic_cluster']], left_on = 'itemId', right_on = 'itemID', how = 'left')

# merge recs with feature
rec = rec.merge(clusters[['itemID', 'main_topic_cluster']], left_on = 'rec_id', right_on = 'itemID', how = 'left')

# rename columns 
rec = rec.rename(columns= {'main_topic_cluster_x': 'main_topic_cluster_item',
                                        #'pageCount_scaled_x': 'pageCount_scaled_item',
                                    'main_topic_cluster_y': 'main_topic_cluster_rec'
                                        #'pageCount_scaled_y': 'pageCount_scaled_rec'
                                                              })
# drop unnecessary columns
rec = rec.drop(['itemID_x', 'itemID_y'], axis = 1)


In [209]:
#############################################

In [36]:
# create features out of data on book categories

categories_match = rec.loc[rec['g_categories_item'].notnull()]
categories_match = categories_match.reset_index()

In [37]:
rec['category_match'] = create_categories_match(categories_match)

In [212]:
#rec = pd.merge(rec, categories_match[['itemId', 'rec_id', 'category_match' ]], on= ['itemId', 'rec_id'], how='left')

#### count main topic and subtopics matches

In [213]:
#rec['main_topic_match'] = create_main_topic_match(rec)

In [214]:
#rec['main_topic_seqmatch'] = create_main_topic_levenshtein(rec)

In [215]:
rec['source'].nunique()

15

In [38]:
rec[['suptopics_matches_count', 'suptopics_matches_weight']] = count_subtopic_matches(rec)

subtopics_item    []
subtopics_item    []
Name: 0, dtype: object
subtopics_rec    []
subtopics_rec    []
Name: 0, dtype: object
one is too shortsubtopics_item    []
subtopics_item    []
Name: 0, dtype: object, subtopics_rec    []
subtopics_rec    []
Name: 0, dtype: object
subtopics_item    []
subtopics_item    []
Name: 1, dtype: object
subtopics_rec    []
subtopics_rec    []
Name: 1, dtype: object
one is too shortsubtopics_item    []
subtopics_item    []
Name: 1, dtype: object, subtopics_rec    []
subtopics_rec    []
Name: 1, dtype: object
subtopics_item    []
subtopics_item    []
Name: 2, dtype: object
subtopics_rec    []
subtopics_rec    []
Name: 2, dtype: object
one is too shortsubtopics_item    []
subtopics_item    []
Name: 2, dtype: object, subtopics_rec    []
subtopics_rec    []
Name: 2, dtype: object
subtopics_item    []
subtopics_item    []
Name: 3, dtype: object
subtopics_rec    []
subtopics_rec    []
Name: 3, dtype: object
one is too shortsubtopics_item    []
subtopics_item  

Name: 32, dtype: object
subtopics_rec    []
subtopics_rec    []
Name: 32, dtype: object
one is too shortsubtopics_item    []
subtopics_item    []
Name: 32, dtype: object, subtopics_rec    []
subtopics_rec    []
Name: 32, dtype: object
subtopics_item    []
subtopics_item    []
Name: 33, dtype: object
subtopics_rec    []
subtopics_rec    []
Name: 33, dtype: object
one is too shortsubtopics_item    []
subtopics_item    []
Name: 33, dtype: object, subtopics_rec    []
subtopics_rec    []
Name: 33, dtype: object
subtopics_item    []
subtopics_item    []
Name: 34, dtype: object
subtopics_rec    []
subtopics_rec    []
Name: 34, dtype: object
one is too shortsubtopics_item    []
subtopics_item    []
Name: 34, dtype: object, subtopics_rec    []
subtopics_rec    []
Name: 34, dtype: object
subtopics_item    [FL]
subtopics_item    [FL]
Name: 35, dtype: object
subtopics_rec    [FL]
subtopics_rec    [FL]
Name: 35, dtype: object
one is too shortsubtopics_item    [FL]
subtopics_item    [FL]
Name: 35, d

subtopics_item    [5AQ,YFE,YFG]
subtopics_item    [5AQ,YFE,YFG]
Name: 64, dtype: object
subtopics_rec    [5AN,YFE]
subtopics_rec    [5AN,YFE]
Name: 64, dtype: object
one is too shortsubtopics_item    [5AQ,YFE,YFG]
subtopics_item    [5AQ,YFE,YFG]
Name: 64, dtype: object, subtopics_rec    [5AN,YFE]
subtopics_rec    [5AN,YFE]
Name: 64, dtype: object
subtopics_item    [5AQ,YFE,YFG]
subtopics_item    [5AQ,YFE,YFG]
Name: 65, dtype: object
subtopics_rec    [5AJ,1FBS,YFM]
subtopics_rec    [5AJ,1FBS,YFM]
Name: 65, dtype: object
one is too shortsubtopics_item    [5AQ,YFE,YFG]
subtopics_item    [5AQ,YFE,YFG]
Name: 65, dtype: object, subtopics_rec    [5AJ,1FBS,YFM]
subtopics_rec    [5AJ,1FBS,YFM]
Name: 65, dtype: object
subtopics_item    [5AQ,YFE,YFG]
subtopics_item    [5AQ,YFE,YFG]
Name: 66, dtype: object
subtopics_rec     []
subtopics_rec    NaN
Name: 66, dtype: object
one is too shortsubtopics_item    [5AQ,YFE,YFG]
subtopics_item    [5AQ,YFE,YFG]
Name: 66, dtype: object, subtopics_rec     []
su

subtopics_item    []
subtopics_item    []
Name: 105, dtype: object
subtopics_rec    []
subtopics_rec    []
Name: 105, dtype: object
one is too shortsubtopics_item    []
subtopics_item    []
Name: 105, dtype: object, subtopics_rec    []
subtopics_rec    []
Name: 105, dtype: object
subtopics_item    []
subtopics_item    []
Name: 106, dtype: object
subtopics_rec    []
subtopics_rec    []
Name: 106, dtype: object
one is too shortsubtopics_item    []
subtopics_item    []
Name: 106, dtype: object, subtopics_rec    []
subtopics_rec    []
Name: 106, dtype: object
subtopics_item    []
subtopics_item    []
Name: 107, dtype: object
subtopics_rec    []
subtopics_rec    []
Name: 107, dtype: object
one is too shortsubtopics_item    []
subtopics_item    []
Name: 107, dtype: object, subtopics_rec    []
subtopics_rec    []
Name: 107, dtype: object
subtopics_item    []
subtopics_item    []
Name: 108, dtype: object
subtopics_rec    []
subtopics_rec    []
Name: 108, dtype: object
one is too shortsubtopics

Name: 144, dtype: object
subtopics_rec    [5AG,WZG,YBCH,YBG,YBL,YZG,YZS]
subtopics_rec    [5AG,WZG,YBCH,YBG,YBL,YZG,YZS]
Name: 144, dtype: object
one is too shortsubtopics_item    [5AG,WZG,YBCH,YBG,YZG,YZS]
subtopics_item    [5AG,WZG,YBCH,YBG,YZG,YZS]
Name: 144, dtype: object, subtopics_rec    [5AG,WZG,YBCH,YBG,YBL,YZG,YZS]
subtopics_rec    [5AG,WZG,YBCH,YBG,YBL,YZG,YZS]
Name: 144, dtype: object
subtopics_item    [5AG,WZG,YBCH,YBG,YZG,YZS]
subtopics_item    [5AG,WZG,YBCH,YBG,YZG,YZS]
Name: 145, dtype: object
subtopics_rec    [WZG,YBG,YDA,YZG]
subtopics_rec    [WZG,YBG,YDA,YZG]
Name: 145, dtype: object
one is too shortsubtopics_item    [5AG,WZG,YBCH,YBG,YZG,YZS]
subtopics_item    [5AG,WZG,YBCH,YBG,YZG,YZS]
Name: 145, dtype: object, subtopics_rec    [WZG,YBG,YDA,YZG]
subtopics_rec    [WZG,YBG,YDA,YZG]
Name: 145, dtype: object
subtopics_item    [5AG,WZG,YBCH,YBG,YZG,YZS]
subtopics_item    [5AG,WZG,YBCH,YBG,YZG,YZS]
Name: 146, dtype: object
subtopics_rec    [5AC,Y,YBL]
subtopics_rec    [5A

...

subtopics_item    [FL]
subtopics_item    [FL]
Name: 10842, dtype: object
subtopics_rec    [FL]
subtopics_rec    [FL]
Name: 10842, dtype: object
one is too shortsubtopics_item    [FL]
subtopics_item    [FL]
Name: 10842, dtype: object, subtopics_rec    [FL]
subtopics_rec    [FL]
Name: 10842, dtype: object
subtopics_item    [FL]
subtopics_item    [FL]
Name: 10843, dtype: object
subtopics_rec    [FL]
subtopics_rec    [FL]
Name: 10843, dtype: object
one is too shortsubtopics_item    [FL]
subtopics_item    [FL]
Name: 10843, dtype: object, subtopics_rec    [FL]
subtopics_rec    [FL]
Name: 10843, dtype: object
subtopics_item    [FL]
subtopics_item    [FL]
Name: 10844, dtype: object
subtopics_rec    [FL]
subtopics_rec    [FL]
Name: 10844, dtype: object
one is too shortsubtopics_item    [FL]
subtopics_item    [FL]
Name: 10844, dtype: object, subtopics_rec    [FL]
subtopics_rec    [FL]
Name: 10844, dtype: object
subtopics_item    [YFP,YXD]
subtopics_item    [YFP,YXD]
Name: 10845, dtype: object
su

subtopics_item    [5AJ,WHJ,YBL,YNT]
subtopics_item                  NaN
Name: 10883, dtype: object
subtopics_rec    [5AJ,1A,WDKN,WDKX,YBG,YBL,YNNL]
subtopics_rec    [5AJ,1A,WDKN,WDKX,YBG,YBL,YNNL]
Name: 10883, dtype: object
one is too shortsubtopics_item    [5AJ,WHJ,YBL,YNT]
subtopics_item                  NaN
Name: 10883, dtype: object, subtopics_rec    [5AJ,1A,WDKN,WDKX,YBG,YBL,YNNL]
subtopics_rec    [5AJ,1A,WDKN,WDKX,YBG,YBL,YNNL]
Name: 10883, dtype: object
subtopics_item    [5AJ,WHJ,YBL,YNT]
subtopics_item                  NaN
Name: 10884, dtype: object
subtopics_rec    [5AJ,WDKX,YBL]
subtopics_rec    [5AJ,WDKX,YBL]
Name: 10884, dtype: object
one is too shortsubtopics_item    [5AJ,WHJ,YBL,YNT]
subtopics_item                  NaN
Name: 10884, dtype: object, subtopics_rec    [5AJ,WDKX,YBL]
subtopics_rec    [5AJ,WDKX,YBL]
Name: 10884, dtype: object
subtopics_item    [5AJ,WHJ,YBL,YNT]
subtopics_item                  NaN
Name: 10885, dtype: object
subtopics_rec    [5AD,5AF,5AG,5AH,4CA,2

subtopics_item    [5AL,5AX,1DST-IT-NVE,YFC,YFH]
subtopics_item    [5AL,5AX,1DST-IT-NVE,YFC,YFH]
Name: 10923, dtype: object
subtopics_rec    [5AL,5AX,5HRB,1DNC,YFC,YFH,3MRB]
subtopics_rec    [5AL,5AX,5HRB,1DNC,YFC,YFH,3MRB]
Name: 10923, dtype: object
one is too shortsubtopics_item    [5AL,5AX,1DST-IT-NVE,YFC,YFH]
subtopics_item    [5AL,5AX,1DST-IT-NVE,YFC,YFH]
Name: 10923, dtype: object, subtopics_rec    [5AL,5AX,5HRB,1DNC,YFC,YFH,3MRB]
subtopics_rec    [5AL,5AX,5HRB,1DNC,YFC,YFH,3MRB]
Name: 10923, dtype: object
subtopics_item    [5AL,5AX,1DST-IT-NVE,YFC,YFH]
subtopics_item    [5AL,5AX,1DST-IT-NVE,YFC,YFH]
Name: 10924, dtype: object
subtopics_rec    [5AL,1DND]
subtopics_rec    [5AL,1DND]
Name: 10924, dtype: object
one is too shortsubtopics_item    [5AL,5AX,1DST-IT-NVE,YFC,YFH]
subtopics_item    [5AL,5AX,1DST-IT-NVE,YFC,YFH]
Name: 10924, dtype: object, subtopics_rec    [5AL,1DND]
subtopics_rec    [5AL,1DND]
Name: 10924, dtype: object
subtopics_item    [5AL,5AX,1DST-IT-NVE,YFC,YFH]
subtop

subtopics_item    [5AG,YBG,YZG]
subtopics_item    [5AG,YBG,YZG]
Name: 10962, dtype: object
subtopics_rec    [5AF,5JA,5JB,5LB,4CD,FN,VXQM1,VXQM4,YBGC,YBLD,...
subtopics_rec                                                  NaN
Name: 10962, dtype: object
one is too shortsubtopics_item    [5AG,YBG,YZG]
subtopics_item    [5AG,YBG,YZG]
Name: 10962, dtype: object, subtopics_rec    [5AF,5JA,5JB,5LB,4CD,FN,VXQM1,VXQM4,YBGC,YBLD,...
subtopics_rec                                                  NaN
Name: 10962, dtype: object
subtopics_item    [5AG,YBG,YZG]
subtopics_item    [5AG,YBG,YZG]
Name: 10963, dtype: object
subtopics_rec    [5AG,YBL]
subtopics_rec    [5AG,YBL]
Name: 10963, dtype: object
one is too shortsubtopics_item    [5AG,YBG,YZG]
subtopics_item    [5AG,YBG,YZG]
Name: 10963, dtype: object, subtopics_rec    [5AG,YBL]
subtopics_rec    [5AG,YBL]
Name: 10963, dtype: object
subtopics_item    [5AG,YBG,YZG]
subtopics_item    [5AG,YBG,YZG]
Name: 10964, dtype: object
subtopics_rec    [5AG,YBG]


Name: 11002, dtype: object
subtopics_rec    []
subtopics_rec    []
Name: 11002, dtype: object
one is too shortsubtopics_item    []
subtopics_item    []
Name: 11002, dtype: object, subtopics_rec    []
subtopics_rec    []
Name: 11002, dtype: object
subtopics_item    [5AN,1DTF,2AJBL,YFB,YFT,YN]
subtopics_item    [5AN,1DTF,2AJBL,YFB,YFT,YN]
Name: 11003, dtype: object
subtopics_rec    [5AN,YFT]
subtopics_rec    [5AN,YFT]
Name: 11003, dtype: object
one is too shortsubtopics_item    [5AN,1DTF,2AJBL,YFB,YFT,YN]
subtopics_item    [5AN,1DTF,2AJBL,YFB,YFT,YN]
Name: 11003, dtype: object, subtopics_rec    [5AN,YFT]
subtopics_rec    [5AN,YFT]
Name: 11003, dtype: object
subtopics_item    [5AN,1DTF,2AJBL,YFB,YFT,YN]
subtopics_item    [5AN,1DTF,2AJBL,YFB,YFT,YN]
Name: 11004, dtype: object
subtopics_rec    [5AN,1DSE-ES-MAA,YFM,YFT,YFY,3MPQM]
subtopics_rec    [5AN,1DSE-ES-MAA,YFM,YFT,YFY,3MPQM]
Name: 11004, dtype: object
one is too shortsubtopics_item    [5AN,1DTF,2AJBL,YFB,YFT,YN]
subtopics_item    [5AN

#### check if main topic cluster is the same

In [218]:
rec['main_topic_cluster_match'] = create_main_topic_cluster_match(rec)

##### book ratings

In [219]:
# get rating columns to float so you can calculate
# fill all NaN with 0 to calculate with it
items_ex['f_average_rating'] = pd.to_numeric(items_ex["f_average_rating"], downcast="float")
#items_ex['f_average_rating'] = items_ex["f_average_rating"].fillna(0)
items_ex['f_ratings_count'] = pd.to_numeric(items_ex["f_ratings_count"], downcast="float")
#items_ex['f_ratings_count'] = items_ex["f_ratings_count"].fillna(0)
items_ex['g_averageRating'] = pd.to_numeric(items_ex["g_averageRating"], downcast="float")
#items_ex['g_averageRating'] = items_ex["g_averageRating"].fillna(0)
items_ex['g_ratingsCount'] = pd.to_numeric(items_ex["g_ratingsCount"], downcast="float")
#items_ex['g_ratingsCount'] = items_ex["g_ratingsCount"].fillna(0)

In [220]:
# calculate total number of ratings
items_ex['total_ratings_count'] = items_ex['f_ratings_count'] + items_ex['g_ratingsCount']
items_ex['total_ratings_count'].replace(0, np.nan, inplace=True)

In [221]:
# calculate weighted average of overall ratings
items_ex['weighted_average_rating'] = (items_ex['f_average_rating']*items_ex['f_ratings_count'] + items_ex['g_averageRating']*items_ex['g_ratingsCount'])/items_ex['total_ratings_count']

In [222]:
### min max normalization for count rating
# apply log to get out skweness of the total rating counts
items_ex['total_ratings_count_log'] = np.log(items_ex['total_ratings_count'])
values = items_ex['total_ratings_count_log']
min_max_scaler = preprocessing.MinMaxScaler()
null_index = items_ex['total_ratings_count'].isnull()
items_ex.loc[~null_index, ['total_ratings_count_log_scaled']] = min_max_scaler.fit_transform(items_ex.loc[~null_index, ['total_ratings_count_log']])
#GoogleBooks['pageCount_scaled'] = GoogleBooks['pageCount']

/Users/MaxLangeMac/opt/anaconda3/lib/python3.8/site-packages/pandas/core/series.py:726: RuntimeWarning: invalid value encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


In [223]:
# merge the book rating features with recs of recommendation data set
rec = rec.merge(items_ex[['itemID', 'weighted_average_rating', 'total_ratings_count', 'total_ratings_count_log_scaled']], left_on = 'rec_id', right_on = 'itemID', how ='left')

In [224]:
rec.shape

(11030, 40)

In [225]:
rec['itemId'].nunique()

1000

##### publish date

In [226]:
#items_ex['year'] = get_publish_year(items_ex)

In [227]:
### get publish year of item and rec
'''
# merge items with feature
rec = rec.merge(items_ex[['itemID', 'year']], left_on = 'itemId', right_on = 'itemID', how = 'left')

# merge recs with feature
rec = rec.merge(items_ex[['itemID', 'year']], left_on = 'rec_id', right_on = 'itemID', how = 'left')

# rename columns 
rec = rec.rename(columns= {'year_x': 'year_item',
                                       'year_y': 'year_rec'})
# drop unnecessary columns
rec = rec.drop(['itemID_x', 'itemID_y'], axis = 1)
'''

"\n# merge items with feature\nrec = rec.merge(items_ex[['itemID', 'year']], left_on = 'itemId', right_on = 'itemID', how = 'left')\n\n# merge recs with feature\nrec = rec.merge(items_ex[['itemID', 'year']], left_on = 'rec_id', right_on = 'itemID', how = 'left')\n\n# rename columns \nrec = rec.rename(columns= {'year_x': 'year_item',\n                                       'year_y': 'year_rec'})\n# drop unnecessary columns\nrec = rec.drop(['itemID_x', 'itemID_y'], axis = 1)\n"

In [228]:
#rec['years_rec_older_than_item'] = rec['year_rec'] - rec['year_item']

In [229]:
rec.shape

(11030, 40)

##### Natalie's code on Price feature

In [230]:
import pandas as pd
import numpy as np
from sklearn import preprocessing

#Distances
def Euclidean_Dist(df1, col1 = ['prices_mean_item'], col2= ['prices_mean_rec']):
    return pd.DataFrame(np.linalg.norm(df1[col1].values - df1[col2].values, axis=1), columns = ['eucl_distance'])

'''Just change data (final result) and ext (external data)'''
#data = pd.read_pickle("recommendations_all_level2_features.pkl")
#data = data.rename(columns = {'itemId': 'itemID'})
#ext = pd.read_pickle("External Data_incl Features.pkl")

data = rec
ext = items_ex

#Rec
data = data.merge(ext[['itemID', 'prices']], left_on = 'rec_id', right_on = 'itemID', how = 'left', suffixes = ['', '_merge'])
data = data.drop(columns = 'itemID')

#Nans need to be filled with empty lists
data = data.reset_index(drop = True)
data.loc[data['prices'].isnull(),['prices']] = data.loc[data['prices'].isnull(),'prices'].apply(lambda x: [])

data.prices = data.prices.apply(lambda x: list(filter(lambda entry: entry != 'EUR', x)))


df = pd.DataFrame(data['prices'].to_list(), columns = ['p_0', 'p_1'])
df = df.replace('EUR', np.nan)

data = pd.concat([data.reset_index(drop = True), df.reset_index(drop = True)], axis = 1)

data = data.dropna(axis = 1, how = 'all')
data.loc[(data['p_0'].isnull()) & (data['p_1'].notnull()), 'p_0'] = data['p_1']
data.loc[(data['p_0'].notnull()) & (data['p_1'].notnull()), 'p_0'] = (data['p_0'] + data['p_1']) / 2
data = data.drop(columns = ['p_1', 'prices'])

data = data.rename(columns = {'p_0': 'prices_mean_rec'})


#item
data = data.merge(ext[['itemID', 'prices']], left_on = 'itemId', right_on = 'itemID', how = 'left', suffixes = ['', '_merge'])
data = data.drop(columns = 'itemID')

data.loc[data['prices'].isnull(),['prices']] = data.loc[data['prices'].isnull(),'prices'].apply(lambda x: [])

data.prices = data.prices.apply(lambda x: list(filter(lambda entry: entry != 'EUR', x)))


df = pd.DataFrame(data['prices'].to_list(), columns = ['p_0', 'p_1'])
df = df.replace('EUR', np.nan)

data = pd.concat([data.reset_index(drop = True), df.reset_index(drop = True)], axis = 1)

data = data.dropna(axis = 1, how = 'all')
data.loc[(data['p_0'].isnull()) & (data['p_1'].notnull()), 'p_0'] = data['p_1']
data.loc[(data['p_0'].notnull()) & (data['p_1'].notnull()), 'p_0'] = (data['p_0'] + data['p_1']) / 2
data = data.drop(columns = ['p_1', 'prices'])

data = data.rename(columns = {'p_0': 'prices_mean_item'})

data = pd.concat([data.reset_index(drop = True), Euclidean_Dist(data).reset_index(drop = True)], axis = 1)

data['rel_distance'] = data['eucl_distance']/data[["prices_mean_item", "prices_mean_rec"]].max(axis=1)

#Scale
x = data[['rel_distance']].values #returns a numpy array
min_max_scaler = preprocessing.MinMaxScaler()
x_scaled = min_max_scaler.fit_transform(x)
df = pd.DataFrame(x_scaled)
df.columns = ['score']

#Append
data = pd.concat([data.reset_index(drop = True), df.reset_index(drop = True)], axis = 1)

data.to_pickle('includingPrices.pkl')

#example = pd.read_pickle("rec_feature_pages.pkl")

rec = data

### Load Haos Cover Feature

In [233]:
# load Haos feature

cover_hao = pd.read_csv('cover_similarity_score_squared.csv')

In [234]:
cover_hao.head()

itemId  rec_id  cover_similarity_score_squared
0      12   50607                        0.969316
1      12   75432                        0.713749
2      12   60328                        0.619374
3      12   72230                        0.369254
4      12   65244                        0.346729

In [235]:
rec.head()

Unnamed: 0  itemId  rec_id  weight            source       title_x  \
0       11174      12   65244    0.25  itemssimilarity_  Breathtaking   
1       11175      12   17952    0.25       clustering_  Breathtaking   
2       11176      12   72230    0.20  itemssimilarity_  Breathtaking   
3       11177      12   30847    0.20       clustering_  Breathtaking   
4       11178      12   28265    0.15  itemssimilarity_  Breathtaking   

              author_x publisher_x main_topic_item subtopics_item  ...  \
0  Reva Ryann Thompson     Xlibris              FM             []  ...   
1  Reva Ryann Thompson     Xlibris              FM             []  ...   
2  Reva Ryann Thompson     Xlibris              FM             []  ...   
3  Reva Ryann Thompson     Xlibris              FM             []  ...   
4  Reva Ryann Thompson     Xlibris              FM             []  ...   

  suptopics_matches_weight main_topic_cluster_match weighted_average_rating  \
0                      0.0                      1.0                     NaN   
1                      0.0                      1.0                     NaN   
2                      0.0                      0.0                     NaN   
3                      0.0                      1.0                     NaN   
4                      0.0                      0.0                     NaN   

  total_ratings_count total_ratings_count_log_scaled  itemID_merge  \
0                 NaN                            NaN       65244.0   
1                 NaN                            NaN       17952.0   
2                 NaN                            NaN       72230.0   
3                 NaN                            NaN       30847.0   
4                 NaN                            NaN       28265.0   

   prices_mean_rec  prices_mean_item  eucl_distance     score  
0              NaN             9.085            NaN       NaN  
1              NaN             9.085            NaN       NaN  
2             3.63             9.085          5.455  0.666463  
3              NaN             9.085            NaN       NaN  
4             4.54             9.085          4.545  0.555284  

[5 rows x 44 columns]

In [236]:
rec_cover_hao = pd.merge(rec, cover_hao,  how='left', left_on=['itemId','rec_id'], right_on = ['itemId','rec_id'])

In [237]:
rec = rec_cover_hao

In [238]:
items_ex.columns

Index(['index', 'itemID', 'title', 'author', 'publisher', 'main topic',
       'subtopics', 'isbn', 'g_description', 'g_maturityRating',
       'g_saleability', 'g_isEbook', 'g_averageRating', 'g_ratingsCount',
       'g_textSnippet', 'g_categories', 'f_average_rating', 'f_ratings_count',
       'f_text_reviews_count', 'f_description', 'a_binding', 'titles',
       'authors', 'publishers', 'images', 'similarBooks', 'dates', 'pages',
       'prices', 'countries', 'languages', 'otherLinks', 'additonalTitles',
       'pages1', 'pages2', 'pages_mean', 'total_ratings_count',
       'weighted_average_rating', 'total_ratings_count_log',
       'total_ratings_count_log_scaled'],
      dtype='object')

In [242]:
## now all features are included

In [244]:
rec.columns

Index(['Unnamed: 0', 'itemId', 'rec_id', 'weight', 'source', 'title_x',
       'author_x', 'publisher_x', 'main_topic_item', 'subtopics_item',
       'title_y', 'author_y', 'publisher_y', 'main_topic_rec', 'subtopics_rec',
       'confItemVsRec', 'titleLength', 'identical', 'pages_mean_item',
       'pages_mean_rec', 'max_pageCount', 'Euc_distance', 'rel_distance',
       'score', 'g_categories_item', 'g_categories_rec', 'main_topic_item',
       'main_topic_rec', 'subtopics_item', 'subtopics_rec',
       'main_topic_cluster_item', 'main_topic_cluster_rec', 'category_match',
       'suptopics_matches_count', 'suptopics_matches_weight',
       'main_topic_cluster_match', 'weighted_average_rating',
       'total_ratings_count', 'total_ratings_count_log_scaled', 'itemID_merge',
       'prices_mean_rec', 'prices_mean_item', 'eucl_distance', 'score',
       'cover_similarity_score_squared'],
      dtype='object')

In [245]:
### save the so far recommendations 
with open('recommendations_all_level2_features.pkl', 'wb') as f:
    pickle.dump(rec, f)